# Unicorn companies




High-growth companies are interested in understanding which industries are producing the highest valuations and the rate at which new high-value companies are emerging. Providing them with this information gives them a competitive insight as to industry trends and how they should structure their portfolio looking forward.

The `unicorns` database contains the following tables:

## dates
| Column       | Description                                  |
|------------- |--------------------------------------------- |
| `company_id`   | A unique ID for the company.                 |
| `date_joined` | The date that the company became a unicorn.  |
| `year_founded` | The year that the company was founded.       |

## funding
| Column           | Description                                  |
|----------------- |--------------------------------------------- |
| `company_id`       | A unique ID for the company.                 |
| `valuation`        | Company value in US dollars.                 |
| `funding`          | The amount of funding raised in US dollars.  |
| `select_investors` | A list of key investors in the company.      |

## industries
| Column       | Description                                  |
|------------- |--------------------------------------------- |
| `company_id`   | A unique ID for the company.                 |
| `industry`     | The industry that the company operates in.   |

## companies
| Column       | Description                                       |
|------------- |-------------------------------------------------- |
| `company_id`   | A unique ID for the company.                      |
| `company`      | The name of the company.                          |
| `city`         | The city where the company is headquartered.      |
| `country`      | The country where the company is headquartered.   |
| `continent`    | The continent where the company is headquartered. |


# The output

Your query should return a table in the following format:
| industry  | year | num\_unicorns       | average\_valuation\_billions |
| --------- | ---- | ------------------- | ---------------------------- |
| industry1 | 2021 |        ---          |             ---              |
| industry2 | 2020 |        ---          |             ---              |
| industry3 | 2019 |        ---          |             ---              |
| industry1 | 2021 |        ---          |             ---              |
| industry2 | 2020 |        ---          |             ---              |
| industry3 | 2019 |        ---          |             ---              |
| industry1 | 2021 |        ---          |             ---              |
| industry2 | 2020 |        ---          |             ---              |
| industry3 | 2019 |        ---          |             ---              |

Where `industry1`, `industry2`, and `industry3` are the three top-performing industries.

In [7]:
-- Analyzing the top-3 best performing industries based on the number of new unicorn companies created in 2019-2021 in the United States
WITH table0 AS (
	SELECT d.company_id, d.date_joined, i.industry, f.valuation/(1 * 10^9) AS valuation_billions
	FROM dates d
	LEFT JOIN 
		industries i ON d.company_id = i.company_id
	LEFT JOIN
		funding f ON d.company_id = f.company_id
),
table1 AS (
	SELECT 
		COUNT (*) AS num_unicorns,
		industry,
		ROUND(AVG(valuation_billions)::numeric, 2) AS average_valuation_billions,
		EXTRACT(year FROM date_joined) AS year
		
	FROM table0
	GROUP BY EXTRACT(year FROM date_joined), industry
	HAVING EXTRACT(year FROM date_joined) BETWEEN 2019 and 2021
),
table2 AS (
    SELECT
        num_unicorns,
        industry,
        year,
        ROW_NUMBER() OVER (PARTITION BY year ORDER BY num_unicorns DESC) AS rank,
		average_valuation_billions
    FROM table1
),
table3 AS (
	SELECT industry, year, num_unicorns, average_valuation_billions
	FROM table2
	WHERE rank < 5 AND industry in ('Fintech', 'Internet software & services', 'E-commerce & direct-to-consumer')
	ORDER BY year DESC, num_unicorns DESC
)
SELECT * 
FROM table3;

industry  ...  average_valuation_billions
0                          Fintech  ...                        2.75
1     Internet software & services  ...                        2.15
2  E-commerce & direct-to-consumer  ...                        2.47
3     Internet software & services  ...                        4.35
4  E-commerce & direct-to-consumer  ...                        4.00
5                          Fintech  ...                        4.33
6                          Fintech  ...                        6.80
7     Internet software & services  ...                        4.23
8  E-commerce & direct-to-consumer  ...                        2.58

[9 rows x 4 columns]

In [26]:
-- Investor analysis 

-- Finding most prevalent investors

WITH investor_list AS (
    SELECT 
        TRIM(UNNEST(STRING_TO_ARRAY("select_investors", ','))) AS investor_name
    FROM 
        funding
),
by_investor AS (
	SELECT 
		i.investor_name,
		f.company_id
	FROM 
		investor_list i
	JOIN 
		funding f 
	ON 
		f.select_investors LIKE CONCAT('%', i.investor_name, '%')
),
by_investor_final AS (
	SELECT 
		investor_name,
		STRING_AGG(company_id::text, ', ') AS company_ids
	FROM by_investor
	GROUP BY investor_name
),
investor_counts AS (
	SELECT 
		investor_name,
		COUNT(*) AS occurrences
	FROM 
		investor_list
	GROUP BY 
		investor_name
	ORDER BY 
		occurrences DESC
),
top_companies AS (
	SELECT 
		company_id,
		RANK() OVER (ORDER BY valuation DESC) AS rank_a,
		select_investors
	FROM funding
	LIMIT 10
),
top_investors AS (
	SELECT TRIM(UNNEST(STRING_TO_ARRAY("select_investors", ','))) AS investor_name
	FROM top_companies
),
-- Analyzing top invested industry for each investor
industry_counts AS (
	SELECT 
		bi.investor_name,
		COUNT(bi.company_id) AS portfolio,
		i.industry
	FROM 
		by_investor bi
	LEFT JOIN
		industries i ON i.company_id = bi.company_id
	GROUP BY 
		bi.investor_name, i.industry
),
ranked_industries AS (
	SELECT
		investor_name,
		industry,
		portfolio,
		ROW_NUMBER() OVER (PARTITION BY investor_name ORDER BY portfolio DESC) AS rn
	FROM 
		industry_counts
),
top_industries AS (
	SELECT
	investor_name,
	industry
FROM
	ranked_industries
WHERE
	rn = 1
)
-- Adding a column to check whether an investor put their money into one of the top companies
SELECT
	il.investor_name,
	ic.occurrences AS no_investment_recepients,
	CASE
		WHEN il.investor_name IN (SELECT investor_name FROM top_investors) THEN TRUE ELSE FALSE END AS top_investor,
	bif.company_ids,
	ti.industry AS fav_industry
FROM investor_list il
LEFT JOIN
	investor_counts ic ON il.investor_name = ic.investor_name
LEFT JOIN
	by_investor_final bif ON bif.investor_name = il.investor_name
LEFT JOIN 
	top_industries ti ON ti.investor_name = il.investor_name;

	

	


investor_name  ...                  fav_industry
0                       EQT Partners  ...                        Health
1                  Dragonfly Captial  ...                       Fintech
2            Qiming Venture Partners  ...                        Health
3                         DST Global  ...                       Fintech
4                         Blackstone  ...  Internet software & services
...                              ...  ...                           ...
3048      Providence Equity Partners  ...  Internet software & services
3049                 NetEase Capital  ...                       Fintech
3050  Northern Light Venture Capital  ...                       Fintech
3051                       Microsoft  ...                       Fintech
3052                    Bain Capital  ...                       Fintech

[3053 rows x 5 columns]

In [19]:
-- Continent Analysis


-- Finding most represented industries by continent using count of firms
WITH most_common_industry AS (
	SELECT
	c.continent,
	i.industry,
	COUNT(c.company_id) AS number_of_industries,
	DENSE_RANK() OVER (PARTITION BY c.continent ORDER BY COUNT(c.company_id) DESC) AS "rank_a"
FROM companies c
LEFT JOIN 
	industries i ON i.company_id = c.company_id
GROUP BY 
	c.continent, i.industry
),
-- Finding Number of Industries and companies per continent
breakdown AS (
	SELECT
	c.continent,
	COUNT(c.company_id) AS number_of_companies,
	COUNT(DISTINCT i.industry) AS number_of_industries
FROM companies c
LEFT JOIN 
	industries i ON i.company_id = c.company_id
GROUP BY 
	c.continent
),
-- Finding top industry  by revenue per continent
industry_revenue AS (
	SELECT
		c.continent,
		i.industry,
		SUM(f.valuation) AS industry_valuation,
		DENSE_RANK() OVER (PARTITION BY c.continent ORDER BY SUM(f.valuation) DESC) AS rank_v
	FROM companies c
	LEFT JOIN
		funding f ON f.company_id = c.company_id
	LEFT JOIN 
		industries i ON i.company_id = c.company_id
	GROUP BY c.continent, i.industry
),
company_revenue AS (
	SELECT
		c.continent,
		c.company_id,
		DENSE_RANK() OVER (PARTITION BY c.continent ORDER BY SUM(f.valuation) DESC) AS rank_c
	FROM companies c
	LEFT JOIN
		funding f ON f.company_id = c.company_id
	GROUP BY c.continent, c.company_id
),
company_revenue_name AS (
	SELECT 
		cr.continent,
		c.company
	FROM company_revenue cr
	LEFT JOIN
		companies c ON cr.company_id = c.company_id
	WHERE cr.rank_c = 1
)
SELECT
	b.*,
	mci.industry AS most_represented_industry,
	ir.industry AS biggest_indusry_by_rev,
	crn.company AS biggest_company_by_rev
FROM breakdown b 
LEFT JOIN
	(SELECT 
	 	continent, 
	 	industry
	FROM 
	 	most_common_industry
	WHERE 
	 	rank_a = 1) AS mci
	ON mci.continent = b.continent
LEFT JOIN 
	company_revenue_name crn ON crn.continent = b.continent
LEFT JOIN (
	SELECT
		industry,
		continent
	FROM
		industry_revenue
	WHERE rank_v = 1
) AS ir
	ON b.continent = ir.continent;




continent  ...  biggest_company_by_rev
0         Africa  ...                    Wave
1         Africa  ...                    Opay
2           Asia  ...               Bytedance
3         Europe  ...                  Klarna
4  North America  ...                  SpaceX
5        Oceania  ...                   Canva
6  South America  ...                   Rappi
7  South America  ...                 C6 Bank
8  South America  ...             QuintoAndar
9  South America  ...                Creditas

[10 rows x 6 columns]

In [10]:
-- Continental analysis 

-- Finding most represented industry on each continent
WITH most_common_industry AS (
	SELECT
		c.continent,
		i.industry,
		COUNT(c.company_id) AS number_of_firms,
		DENSE_RANK() OVER (PARTITION BY c.continent ORDER BY COUNT(c.company_id) DESC) AS rank_a
	FROM 
		companies c
	LEFT JOIN 
		industries i ON i.company_id = c.company_id
	GROUP BY 
		c.continent, i.industry
),
-- Finding top industry by revenue for each continent
industry_revenue AS (
	SELECT
		c.continent,
		i.industry,
		SUM(f.valuation) AS industry_valuation,
		DENSE_RANK() OVER (PARTITION BY c.continent ORDER BY SUM(f.valuation) DESC) AS rank_v
	FROM 
		companies c
	LEFT JOIN 
		industries i ON i.company_id = c.company_id
	LEFT JOIN 
		funding f ON f.company_id = c.company_id
	GROUP BY 
		c.continent, i.industry
),
-- Finding top company by revenue for each continent 
top_company_revenue AS (
	SELECT
		c.continent,
		c.company,
		DENSE_RANK() OVER (PARTITION BY c.continent ORDER BY SUM(f.valuation) DESC) AS rank_c
	FROM 
		companies c
	LEFT JOIN 
		funding f ON f.company_id = c.company_id
	GROUP BY 
		c.continent, c.company_id
)

-- Joining everything together
SELECT
	b.continent,
	COUNT(b.company_id) AS number_of_companies,
	COUNT(DISTINCT i.industry) AS number_of_industries,
	mci.industry AS most_represented_industry,
	ir.industry AS biggest_industry_by_revenue,
	tcr.company AS biggest_company_by_revenue
FROM 
	companies b
LEFT JOIN 
	industries i ON i.company_id = b.company_id
LEFT JOIN 
	(SELECT continent, industry FROM most_common_industry WHERE rank_a = 1) mci ON mci.continent = b.continent
LEFT JOIN 
	(SELECT continent, industry FROM industry_revenue WHERE rank_v = 1) ir ON ir.continent = b.continent
LEFT JOIN 
	(SELECT continent, company FROM top_company_revenue WHERE rank_c = 1) tcr ON tcr.continent = b.continent
GROUP BY 
	b.continent, mci.industry, ir.industry, tcr.company;

continent  ...  biggest_company_by_revenue
0         Africa  ...                        Opay
1         Africa  ...                        Wave
2           Asia  ...                   Bytedance
3         Europe  ...                      Klarna
4  North America  ...                      SpaceX
5        Oceania  ...                       Canva
6  South America  ...                     C6 Bank
7  South America  ...                    Creditas
8  South America  ...                 QuintoAndar
9  South America  ...                       Rappi

[10 rows x 6 columns]